# COVID-19 Data (API).
### COVID-19 Country Data.
[site](https://covid19api.com/) | [API info](https://documenter.getpostman.com/view/10808728/SzS8rjbc?version=latest)


# API

In [49]:
# necessary imports.
import numpy as np
import pandas as pd
import plotly.graph_objects as go

In [67]:
# read in the csv file.
fires = pd.read_csv("https://raw.githubusercontent.com/CVanchieri/DSPortfolio/master/posts/AustraliaBushFiresMapBoxPost/australiabushfires.csv", index_col=0)
print(fires.shape)
fires.head()

(127048, 5)


Date      Lat       Lon  Brightness Day_Night
0  2019-09-01 -12.3168  142.0542       311.4         D
1  2019-09-01 -12.3168  142.0542       310.2         D
2  2019-09-01 -12.3168  142.0542       310.1         D
3  2019-09-01 -12.3168  142.0542       310.4         D
4  2019-09-01 -12.3168  142.0542       314.3         D

In [68]:
# set the time series and data for frames data.
times = fires.groupby(['Date'])['Date'].count().index.tolist()
frames_data = [fires.loc[fires['Date'] == t] for t in times]
# set the frames for the density mapbox.
frames = [go.Frame(data=[go.Densitymapbox(lat=f['Lat'], lon=f['Lon'], z=f['Brightness'], radius=10)], name=str(f.iloc[0]['Date'])) for f in frames_data]
# create how the map works, buttons, sliders.
buttons=[
         dict(label="Play",method="animate",args=[None, {'fromcurrent':True, "transition": {"duration": 20, "easing": "quadratic-in-out"}}]),
         dict(label="Pause",method="animate",args=[[None], {"frame": {"duration": 0, "redraw": False},"mode": "immediate", "transition": {"duration": 0}}])
]

sliders_dict = {
    'active':0,
    'currentvalue': dict(font=dict(size=15), prefix='Time: ', visible=True),
    "transition": {"duration": 300, "easing": "cubic-in-out"},
    'x': 0,
    'steps': []
}

for i,t in enumerate(times):
    slider_step = {"args": [
                        [t],
                        {"frame": {"duration": 300, "redraw": False},
                         #"mode": "immediate",
                         "transition": {"duration": 30, "easing": "quadratic-in-out"}}
                    ],
            "label": t,
            "method": "animate",
            "value": t
    }
    sliders_dict['steps'].append(slider_step)

In [69]:
# set the mapbox style and access token.
''' style url '''
MAPBOX_STYLE = 'mapbox://styles/cvanchieri/ck922oal90bxw1ilzl8opoz7d'
''' access token '''
MAPBOX_TOKEN = 'pk.eyJ1IjoiY3ZhbmNoaWVyaSIsImEiOiJjazkwcTM3bGwwNGU4M2hucGYxNmkydGFzIn0.sDsBLsY2hw-6LPjKzL2ZqA'

In [70]:
# set the figure layout of the graph.
fig = go.Figure(data = [go.Densitymapbox(lat=fires['Lat'], lon=fires['Lon'], z=fires['Brightness'], radius=5, colorscale='Hot', zmax=300, zmin=0)],
               layout=go.Layout(updatemenus=[dict(type="buttons", buttons=buttons,showactive=True)] ), 
               frames=frames
)
fig.update_layout(mapbox_style=MAPBOX_STYLE, 
                  mapbox_accesstoken=MAPBOX_TOKEN,
                  mapbox_center_lon=135,
                  mapbox_center_lat=-25.34,
                  mapbox_zoom=3.5)
fig.update_layout(sliders=[sliders_dict],
                 title='2019 Australia Bush Fires')
fig.update_layout(height=1000)
fig.show()